In [1]:
import numpy as np
import cv2
import os
import random
import tensorflow as tf
from tensorflow.keras.callbacks import Callback
from tqdm import tqdm
from tensorflow.keras import layers, Model, optimizers


In [2]:
def load_images_from_folder(folder):
    images = []
    for filename in os.listdir(folder):
        file_path = os.path.join(folder, filename)
        if os.path.isdir(file_path):
            continue  # Skip directories
        if not file_path.endswith(('.png', '.jpg', '.jpeg')):
            continue  # Skip non-image files
        
        img = cv2.imread(file_path, cv2.IMREAD_GRAYSCALE)
        if img is not None:
            images.append(img)
    return images

In [3]:
def generate_pairs(dataset_dir):
    pairs = []
    labels = []
    persons = os.listdir(dataset_dir)
    persons = [person for person in persons if os.path.isdir(os.path.join(dataset_dir, person))]

    for person in persons:
        person_dir = os.path.join(dataset_dir, person)
        images = load_images_from_folder(person_dir)
      
        if len(images) < 2:
            continue  
        
        # Positive pairs
        for i in range(len(images)):
            for j in range(i + 1, len(images)):
                pairs.append((images[i], images[j]))
                labels.append(1)
                
        # Negative pairs
        other_persons = [p for p in persons if p != person]
        for i in range(len(images)):
            while True:
                other_person = random.choice(other_persons)
                other_person_dir = os.path.join(dataset_dir, other_person)
                try:
                    other_images = load_images_from_folder(other_person_dir)
                except NotADirectoryError:
                    other_images = []
                if other_images:
                    break  # Ensure we get a non-empty list of images
            if not other_images:
                continue  # Skip if other_images is empty
            
            other_image = random.choice(other_images)
            pairs.append((images[i], other_image))
            labels.append(0)
                
    return np.array(pairs), np.array(labels)


In [4]:
train_dir='/Users/apoorvagayatrik/PerspectAIProj/processed_images_noesrgan/train_ds'
test_dir='/Users/apoorvagayatrik/PerspectAIProj/processed_images_noesrgan/test_ds'
val_dir='/Users/apoorvagayatrik/PerspectAIProj/processed_images_noesrgan/val_ds'

In [5]:
train_pairs, train_labels = generate_pairs(train_dir)
val_pairs, val_labels = generate_pairs(val_dir)
test_pairs, test_labels = generate_pairs(test_dir)

In [6]:
def create_siamese_network(input_shape):
    input = layers.Input(input_shape)
    x = layers.Conv2D(64, (7, 7), activation='relu', padding='same')(input)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(128, (5, 5), activation='relu', padding='same')(x)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(128, (3, 3), activation='relu', padding='same')(x)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(256, (3, 3), activation='relu', padding='same')(x)
    x = layers.Flatten()(x)
    x = layers.Dense(4096, activation='sigmoid')(x)
    return Model(input, x)

In [7]:
class TqdmProgressCallback(Callback):
    def __init__(self, steps_per_epoch):
        super().__init__()
        self.steps_per_epoch = steps_per_epoch

    def on_epoch_begin(self, epoch, logs=None):
        self.progress_bar = tqdm(total=self.steps_per_epoch, desc=f'Epoch {epoch + 1}/{self.params["epochs"]}', unit='step')

    def on_batch_end(self, batch, logs=None):
        self.progress_bar.update(1)

    def on_epoch_end(self, epoch, logs=None):
        self.progress_bar.close()

# Determine steps per epoch
batch_size = 32
steps_per_epoch = len(train_pairs[0]) // batch_size

# Initialize the callback with steps per epoch
progress_callback = TqdmProgressCallback(steps_per_epoch)



In [8]:
input_shape = (64, 64, 1)  # Example input shape
base_network = create_siamese_network(input_shape)


2024-06-27 18:26:14.206262: I metal_plugin/src/device/metal_device.cc:1154] Metal device set to: Apple M2
2024-06-27 18:26:14.206314: I metal_plugin/src/device/metal_device.cc:296] systemMemory: 8.00 GB
2024-06-27 18:26:14.206326: I metal_plugin/src/device/metal_device.cc:313] maxCacheSize: 2.67 GB
2024-06-27 18:26:14.206364: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2024-06-27 18:26:14.206398: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


In [9]:
input_a = layers.Input(shape=input_shape)
input_b = layers.Input(shape=input_shape)


In [10]:
encoded_a = base_network(input_a)
encoded_b = base_network(input_b)



In [11]:
L1_layer = layers.Lambda(lambda tensors: tf.abs(tensors[0] - tensors[1]))
L1_distance = L1_layer([encoded_a, encoded_b])

In [12]:
output = layers.Dense(1, activation='sigmoid')(L1_distance)


In [13]:
siamese_net = Model(inputs=[input_a, input_b], outputs=output)


In [14]:
siamese_net.compile(loss='binary_crossentropy', optimizer=optimizers.Adam(0.0001), metrics=['accuracy'])


In [15]:
def prepare_data(pairs, labels):
    pairs = np.array(pairs, dtype=np.float32)
    pairs = pairs / 255.0  # Normalize to [0, 1]
    labels = np.array(labels, dtype=np.float32)
    return pairs, labels

In [16]:
train_pairs, train_labels = prepare_data(train_pairs, train_labels)
val_pairs, val_labels = prepare_data(val_pairs, val_labels)
test_pairs, test_labels = prepare_data(test_pairs, test_labels)


In [17]:
train_pairs = [train_pairs[:, 0].reshape(-1, 64, 64, 1), train_pairs[:, 1].reshape(-1, 64, 64, 1)]
val_pairs = [val_pairs[:, 0].reshape(-1, 64, 64, 1), val_pairs[:, 1].reshape(-1, 64, 64, 1)]
test_pairs = [test_pairs[:, 0].reshape(-1, 64,64, 1), test_pairs[:, 1].reshape(-1, 64, 64, 1)]

In [18]:
siamese_net.fit([train_pairs[0], train_pairs[1]], train_labels, validation_data=([val_pairs[0], val_pairs[1]], val_labels), batch_size=32, epochs=5, callbacks=[progress_callback])


Epoch 1/5: 0step [00:00, ?step/s]

Epoch 1/5


2024-06-27 18:27:24.033208: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:117] Plugin optimizer for device_type GPU is enabled.
Epoch 1/5: 1step [00:14, 14.11s/step]

   1/2042 ━━━━━━━━━━━━━━━━━━━━ 8:00:00 14s/step - accuracy: 0.7812 - loss: 0.6932

Epoch 1/5: 2step [00:14,  6.11s/step]

...

2041/2042 ━━━━━━━━━━━━━━━━━━━━ 0s 464ms/step - accuracy: 0.9978 - loss: 0.0116

Epoch 5/5: 2042step [15:50,  3.75step/s]

2042/2042 ━━━━━━━━━━━━━━━━━━━━ 0s 464ms/step - accuracy: 0.9978 - loss: 0.0116

Epoch 5/5: 2042step [18:40,  1.82step/s]

2042/2042 ━━━━━━━━━━━━━━━━━━━━ 1121s 547ms/step - accuracy: 0.9978 - loss: 0.0116 - val_accuracy: 0.8469 - val_loss: 0.7274


In [1]:
from tensorflow.keras.models import load_model

# Assuming facenet_model is your trained model
siamese_net.save('siamese_model.keras')


NameError: name 'siamese_net' is not defined

In [23]:
import matplotlib.pyplot as plt
from tensorflow.keras.models import load_model
from tensorflow.keras.callbacks import History

In [19]:
test_loss, test_accuracy = siamese_net.evaluate([test_pairs[0], test_pairs[1]], test_labels)
print(f"Test Loss: {test_loss}")
print(f"Test Accuracy: {test_accuracy}")


1911/1911 ━━━━━━━━━━━━━━━━━━━━ 176s 91ms/step - accuracy: 0.9452 - loss: 0.2678
Test Loss: 0.2618151605129242
Test Accuracy: 0.942380964756012


In [28]:
val_loss, val_accuracy = siamese_net.evaluate([val_pairs[0], val_pairs[1]], val_labels)
print(f"Test Loss: {val_loss}")
print(f"Test Accuracy: {val_accuracy}")


3219/3219 ━━━━━━━━━━━━━━━━━━━━ 287s 87ms/step - accuracy: 0.8590 - loss: 0.7713
Test Loss: 0.6743754744529724
Test Accuracy: 0.8565782904624939
